# Extracting macro-dynamics

We use the termites model to show how macro-dynamics can be extracted.

First, we load the model and build its state-space as a single-node component-graph `g`. Then, we define our target formula: all kind of termites are present.

In [1]:
%run -m ecco rr-termites.rr
g = model()
phi = "(Rp & Sd & Wk)"

Then, we split against two properties: `phi` itself, and `f"EF{phi}"` (where `f"...{phi}..."` allows in Python to insert formula `phi` into another string).

In [2]:
g1 = g.split(phi=phi, EF_phi=f"EF{phi}")
g1

In [3]:
g1.nodes

traps  size                          consts  \
node                                               
1       ()    12  (Ec+, Fg+, Md+, Rp+, Sd+, Wk+)   
3      (1)    34                           (Rp+)   
4       ()    68                      (Rp-, Wk-)   

                                     HASNO     HAS           CONTAINS  \
node                                                                    
1                             (DEAD, INIT)   (scc)             (hull)   
3                              (DEAD, phi)  (HULL)  (INIT, hull, scc)   
4     (EF_phi, HULL, INIT, hull, phi, scc)      ()             (DEAD)   

                ISIN EQUALS  
node                         
1     (EF_phi, HULL)  (phi)  
3           (EF_phi)     ()  
4                 ()     ()

We observe that `phi` is reachable and the corresponding states are in component `#1`, the rest of the state space is split into the states that allow to reach `phi` (`#3`) and those where `phi` has been lost forever (`#4`).

We also observe that `phi` may persist forever since `#1` contains a SCC.

Finally, we observe that `#3` is a trap and we shall fix this:

In [4]:
g2 = g1.untrap(3)
g2

Why `#3` was a trap is now explained: from the initial state, we can reach `#5` then `#1` and obtain `phi`.
But from `#5` and `#1`, the initial state and other states, forming `#6`, cannot be reached back.
This initial part `#6` even contains a SCC, which means that reaching `phi` can be delayed forever.
This is also the case with `#5` and there is only one difference between `#5` and `#6`: the former can be reached from states where `phi` holds while the latter cannot, but both allow to reach `phi` while this may be delayed forever.

We may wan to separate in `#6` the states that allow this delay from the others using functional property `hull()`.

In [6]:
g3 = g2.split("hull()", 6)
g3

Now we can see that the system needs to execute `R4` before it has a chance to reach `phi`.
Then, at any stage, executing `R11` or `R12` is the cause of loosing the reachability of `phi`.
We could further analyse what these transitions are and why `#1` and `#5` are not SCC, but this is not the purpose of this notebokk that just shows how generic splits can provide a reach overview of the macro-dynamics of a system with respect to a property of interest.